In [ ]:
!pip install plotly

In [ ]:
!pip --version

In [ ]:
import sys
print(sys.version)
import numpy as np
import matplotlib.pyplot as plt
import plotly as plotly
import plotly.graph_objects as go
# import ipywidgets as widgets
import base.proto
from prediction.metrics.apps.evaluation_results_pb2 import EvaluationReport

In [ ]:
# https://git.zooxlabs.com/zooxco/driving/blob/master/prediction/metrics/apps/evaluation_results.proto
report_file = '/mnt/nautilus_rw/kdu/metrics/eval.EvalReport.pbtxt'
report = EvaluationReport()
base.proto.ReadProto(report_file, report)
print('report name: ' + report.name)

In [ ]:
import math
from base.report.proto.report_pb2 import ChartProto, SeriesProto

for metric in report.metric:
    if metric.name:
        print('metric name: ' + metric.name)
    else:
        continue
    if metric.area_under_curve:
        print('AUC: {}'.format(metric.area_under_curve))
    # https://git.zooxlabs.com/zooxco/driving/blob/master/vision/utils/proto/evaluation_curve.proto
    len_points = len(metric.pr_point)
    print('num of PR points: {}'.format(len_points))
    dtype = [('precision', float), ('recall', float), ('score', float), ('num_results', int)]
    pr_points = np.empty(len_points, dtype=dtype)
    for i in range(len_points):
        pr_point = metric.pr_point[i]
        pr_points[i] = (pr_point.precision, pr_point.recall, pr_point.score, pr_point.num_results)
    
    np.sort(pr_points, order=['recall'])
    if len(pr_points) > 0 and not math.isnan(metric.area_under_curve):        
        fig = go.Figure()
        fig = fig.add_trace(go.Scatter(
            x=pr_points['recall'], 
            y=pr_points['precision']
        ))
        fig.update_layout(
            title=metric.name,
            xaxis_title='Recall',
            yaxis_title='Precision'
        )
        fig.update_layout(
            autosize=False,
            width=400,
            height=400,
        )
        fig.show()
        
    # positive flicker rate
    positive_flicker_histogram = ChartProto()
    positive_flicker_histogram = metric.positive_flicker_histogram
    hist_x = positive_flicker_histogram.x
    hist_x_vec = []
    for x_val in hist_x.value:
        hist_x_vec.append(x_val)
    hist_y = positive_flicker_histogram.y
    hist_y_vec = []
    # Just get the 1st from the repeated array
    for y_val in hist_y[0].value:
        hist_y_vec.append(y_val)
    fig = go.Figure()
    fig = fig.add_trace(go.Scatter(
        x=hist_x_vec, 
        y=hist_y_vec
    ))
    fig.update_layout(
        title='Positive flicker rate',
        xaxis_title='Flicker fraction',
        yaxis_title='Cumulative histagram'
    )
    fig.update_layout(
        autosize=False,
        width=400,
        height=400,
    )
    fig.show()
    
    # Negative flicker rate
    negative_flicker_histogram = ChartProto()
    negative_flicker_histogram = metric.negative_flicker_histogram
    hist_x = negative_flicker_histogram.x
    hist_x_vec = []
    for x_val in hist_x.value:
        hist_x_vec.append(x_val)
    hist_y = negative_flicker_histogram.y
    hist_y_vec = []
    # Just get the 1st from the repeated array
    for y_val in hist_y[0].value:
        hist_y_vec.append(y_val)
    fig = go.Figure()
    fig = fig.add_trace(go.Scatter(
        x=hist_x_vec, 
        y=hist_y_vec
    ))
    fig.update_layout(
        title='Negative flicker rate',
        xaxis_title='Flicker fraction',
        yaxis_title='Cumulative histagram'
    )
    fig.update_layout(
        autosize=False,
        width=400,
        height=400,
    )
    fig.show()
    
    # time to predict
    time_to_predict = ChartProto()
    time_to_predict = metric.time_to_predict
    hist_x = time_to_predict.x
    hist_x_vec = []
    for x_val in hist_x.value:
        hist_x_vec.append(x_val)
    hist_y = time_to_predict.y
    hist_y_vec = []
    # Just get the 1st from the repeated array
    for y_val in hist_y[0].value:
        hist_y_vec.append(y_val)
    fig = go.Figure()
    fig = fig.add_trace(go.Scatter(
        x=hist_x_vec, 
        y=hist_y_vec
    ))
    fig.update_layout(
        title='Time to Predict',
        xaxis_title='Time-To-Predcit(Seconds)',
        yaxis_title='Cumulative histagram'
    )
    fig.update_layout(
        autosize=False,
        width=400,
        height=400,
    )
    fig.show()
    